In [63]:
import numpy as np
from sympy import *
import matplotlib.pyplot as plt
import pandas as pd
import math
from scipy import signal
import scipy as sy
from numpy.fft import fft, fftshift
import seaborn as sns
#sns.set_style("darkgrid")
plt.style.use('seaborn-dark-palette')
plt.style.use('seaborn-darkgrid')

import chart_studio as py
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly
import cufflinks as cf
init_notebook_mode(connected=True)
cf.go_offline()

In [64]:
user1_1 = pd.DataFrame(data = np.loadtxt('acc_exp01_user01.txt'), columns = ['X','Y','Z'])
user1_2 = pd.DataFrame(data = np.loadtxt("acc_exp02_user01.txt"), columns = ['X','Y','Z'])
user2_1 = pd.DataFrame(data = np.loadtxt("acc_exp03_user02.txt"), columns = ['X','Y','Z'])
user2_2 = pd.DataFrame(data = np.loadtxt("acc_exp04_user02.txt"), columns = ['X','Y','Z'])
user3_1 = pd.DataFrame(data = np.loadtxt("acc_exp05_user03.txt"), columns = ['X','Y','Z'])
user3_2 = pd.DataFrame(data = np.loadtxt("acc_exp06_user03.txt"), columns = ['X','Y','Z'])
user4_1 = pd.DataFrame(data = np.loadtxt("acc_exp07_user04.txt"), columns = ['X','Y','Z'])
user4_2 = pd.DataFrame(data = np.loadtxt("acc_exp08_user04.txt"), columns = ['X','Y','Z'])

fs = 50 # Hz
T = 1/fs # sec

user1_1['Time (min)'] = np.arange(0, len(user1_1['X']) * T, T)/60
user1_2['Time (min)'] = np.arange(0, len(user1_2['X']) * T, T)/60 
user2_1['Time (min)'] = np.arange(0, len(user2_1['X']) * T, T)/60 
user2_2['Time (min)'] = np.arange(0, len(user2_2['X']) * T, T)/60 
user3_1['Time (min)'] = np.arange(0, len(user3_1['X']) * T, T)/60 
user3_2['Time (min)'] = np.arange(0, len(user3_2['X']) * T, T)/60 
user4_1['Time (min)'] = np.arange(0, len(user4_1['X']) * T, T)/60 
user4_2['Time (min)'] = np.arange(0, len(user4_2['X']) * T, T)/60

In [65]:
ax = user4_2.iplot(x = 'Time (min)', size = (10,15))

#ax[1].annotate(text = 'hehexD', xy = (2, 1.5))

In [66]:
#uma segmentação das informações do user, num intervalo [*xi*, *xf*[
def ufrag(user, xi, xf):
    return user[ (xi<=user['Time (min)']) & (user['Time (min)'] < xf) ].reset_index().drop("index", axis = 1)

In [67]:
def detrend_user_walk(user):
    new = user.copy()
    new['X'] = signal.detrend(user['X'])
    new['Y'] = signal.detrend(user['Y'])
    new['Z'] = signal.detrend(user['Z'])
    return new

In [68]:
unow = user1_1
walks_user1_1 = [ ufrag(unow, 2.5, 2.693), ufrag(unow, 2.8, 3.15), ufrag(unow, 3.3, 3.5), ufrag(unow, 3.6, 3.9)]

unow = user1_2
walks_user1_2 = [  ufrag(unow, 2.55, 2.7), ufrag(unow, 2.9, 3.2), ufrag(unow, 3.3, 3.6), ufrag(unow, 3.8, 4.1)]

unow = user2_1
walks_user2_1 = [ ufrag(unow, 2.5, 2.725), ufrag(unow, 2.9, 3.125), ufrag(unow, 3.3, 3.525) ]

unow = user2_2
walks_user2_2 = [ ufrag(unow, 2.2, 2.37), ufrag(unow, 2.5, 2.8), ufrag(unow, 2.9, 3.22) ]

unow = user3_1
walks_user3_1 = [ ufrag(unow, 2.55, 2.7), ufrag(unow, 2.9, 3.2), ufrag(unow, 3.5, 3.7) ]

unow = user3_2
walks_user3_2 = [ ufrag(unow, 2.65, 2.8), ufrag(unow, 2.9, 3.2), ufrag(unow, 3.4, 3.6) ]

unow = user4_1
walks_user4_1 = [ ufrag(unow, 2.5, 2.6), ufrag(unow, 2.7, 3.05), ufrag(unow, 3.2, 3.5) ]

unow = user4_2
walks_user4_2 = [ ufrag(unow, 2.3, 2.5), ufrag(unow, 2.6, 2.9), ufrag(unow, 3.05, 3.3) ]

walks_user1_1_detrended = []
for i in walks_user1_1:
    walks_user1_1_detrended.append( detrend_user_walk(i) )
    
walks_user1_2_detrended = []
for i in walks_user1_2:
    walks_user1_2_detrended.append( detrend_user_walk(i) )
    
walks_user2_1_detrended = []
for i in walks_user2_1:
    walks_user2_1_detrended.append( detrend_user_walk(i) )
    
walks_user2_2_detrended = []
for i in walks_user2_2:
    walks_user2_2_detrended.append( detrend_user_walk(i) )
    
walks_user3_1_detrended = []
for i in walks_user3_1:
    walks_user3_1_detrended.append( detrend_user_walk(i) )

walks_user3_2_detrended = []
for i in walks_user3_2:
    walks_user3_2_detrended.append( detrend_user_walk(i) )

walks_user4_1_detrended = []
for i in walks_user4_1:
    walks_user4_1_detrended.append( detrend_user_walk(i) )
    
walks_user4_2_detrended = []
for i in walks_user4_2:
    walks_user4_2_detrended.append( detrend_user_walk(i) )


In [138]:
def plot_activity_dft(user_frag_act, N, user, exp, title, zeros, percent, wind_title, plotit):
    fs = 50
    if N%2==0:
        f = np.linspace( -fs/2, fs/2 - fs/N, N) 
    else:
        f = np.linspace( -fs/2 + fs/2/N, fs/2 - fs/2/N, N)
    
    if wind_title.lower()=='blackman':
        window = np.blackman(N)
    elif wind_title.lower()=='hamming':
        window = np.hamming(N)
    elif wind_title.lower()=='hann':
        window = signal.windows.hann(N)
    elif wind_title.lower()=='rect':
        window = np.ones(f.shape)
    elif wind_title.lower()=='black_harris':
        window = signal.windows.blackmanharris(N)
    
    dfts = []
    dfts.append( np.abs( fftshift( fft( user_frag_act['X'] * window ) ) ) ) 
    dfts.append( np.abs( fftshift( fft( user_frag_act['Y'] * window ) ) ) )
    dfts.append( np.abs( fftshift( fft( user_frag_act['Z'] * window ) ) ) )
    
    if plotit:
    
        figure, subplots = plt.subplots(nrows = 1, ncols= 3, figsize = (20,5))
        figure.suptitle(f'DFT de {title} - Experiência {exp} do User {user} -- Window: {wind_title}', fontsize = 'xx-large')
    
        if zeros:
            for i in range(3):
                dfts[i][ dfts[i]<np.max(dfts[i])*percent ] = 0
        else:
            for i in range(3):
                subplots[i].plot(f, np.full((len(f),),np.max(dfts[i])*percent), 'r')
        
        for i in range(3):
            marker, stem, base = subplots[i].stem(f, dfts[i])
            stem.set_linewidth(0.8)
            plt.setp(marker, markersize = 2)
        

        subplots[0].set_xlabel("Axis X Frequency (Hz)")
        subplots[1].set_xlabel("Axis Y Frequency (Hz)")
        subplots[2].set_xlabel("Axis Z Frequency (Hz)")
        subplots[0].set_ylabel("Magnitude")
        subplots[1].set_ylabel("Magnitude")
        subplots[2].set_ylabel("Magnitude")
    
        figure.tight_layout()
    if not plotit:
        for i in range(3):
            dfts[i][ dfts[i]<np.max(dfts[i])*percent ] = 0
   
    return np.unique(np.round(np.abs(f[np.where(dfts[0])]), 8)), np.unique(np.round(np.abs(f[np.where(dfts[1])]), 8)), np.unique(np.round(np.abs(f[np.where(dfts[2])]), 8))

In [149]:

x_total = []
y_total = []
z_total = []
walks_user = []

walks_user.append(walks_user1_1_detrended)
walks_user.append(walks_user1_2_detrended)
walks_user.append(walks_user2_1_detrended)
walks_user.append(walks_user2_2_detrended)
walks_user.append(walks_user3_1_detrended)
walks_user.append(walks_user3_2_detrended)
walks_user.append(walks_user4_1_detrended)
walks_user.append(walks_user4_2_detrended)

#print(walks_user)

for a in walks_user:

    for i in range(3):
        x, y, z = plot_activity_dft(a[i], len(a[i]), 1, 1, 'WALK', True, 0.65, 'blackman', False)
        for j in x:
            x_total.append(j)
        for j in y:
            y_total.append(j)
        for j in z:
            z_total.append(j)

            
aux = {'X':x_total, 'Y':y_total, 'Z':z_total}
Hz_pd = pd.DataFrame.from_dict(aux, orient='index').transpose()
Hz_pd = Hz_pd[::][Hz_pd[::]<2.5]
Hz_pd.describe()

X         Y         Z
count  7.000000  7.000000  8.000000
mean   1.817886  1.817886  1.121523
std    0.052163  0.052163  0.434801
min    1.750000  1.750000  0.833333
25%    1.785714  1.785714  0.861954
50%    1.813471  1.813471  0.910714
75%    1.845238  1.845238  1.165803
max    1.899827  1.899827  1.833333